Dataset source: https://archive.ics.uci.edu/ml/datasets/Adult <br/>
PySpark ML Classifier Reference: https://spark.apache.org/docs/2.3.0/ml-classification-regression.html#classification <br/>
<b> <i> Classifier Models Used: </i> </b> <br/>
<ul>
  <li> Logistic Regression </li>
  <li> Naive Bayes </li>
  <li> Decision Tree </li>
  <li> Gradient-boosted Tree </li>
  <li> Random Forest </li>
  <li> Multilayer Perceptron </li>
  <li> One-vs-All (Logistic Regression, Random Forest) </li>
</ul>
<hr/>

In [2]:
# Computational and Visualisation Packages
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from ggplot import *

# Pyspark Packages
from pyspark.sql import functions as F
from pyspark.sql.functions import col, desc, trim
from pyspark.sql.types import *
from pyspark.ml import Pipeline
from pyspark.ml.classification import NaiveBayes, LogisticRegression, DecisionTreeClassifier, GBTClassifier, RandomForestClassifier, OneVsRest, MultilayerPerceptronClassifier
from pyspark.ml.feature import OneHotEncoderEstimator, StringIndexer, VectorAssembler
from pyspark.ml.evaluation import RegressionEvaluator, BinaryClassificationEvaluator, MulticlassClassificationEvaluator
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator

In [3]:
adult_gov_data = spark.read.csv('/databricks-datasets/adult/adult.data')
country_codes = spark.sql('SELECT * FROM country_codes')

adult_gov_data = adult_gov_data.select(col('_c0').cast('double').alias('age'), col('_c1').alias('workclass'), col('_c2').cast('double').alias('fnlwgt'), col('_c3').alias('education'), col('_c4').cast('double').alias('education_num'), col('_c5').alias('marital_status'),col('_c6').alias('occupation'), col('_c7').alias('relationship'), col('_c8').alias('race'), col('_c9').alias('sex'), col('_c10').cast('double').alias('capital_gain'), col('_c11').cast('double').alias('capital_loss'), col('_c12').cast('double').alias('hours_per_week'), col('_c13').alias('native_country'), col('_c14').alias('income'))
adult_gov_data = adult_gov_data.withColumn('native_country', F.regexp_replace(col('native_country'), '-', ' '))
adult_gov_data = adult_gov_data.withColumn('native_country', trim(col('native_country')))

expanded_cols = adult_gov_data.columns + ['alpha_3_code', 'latitude', 'longitude']
adult_gov_data_expanded = adult_gov_data.join(country_codes, adult_gov_data.native_country == country_codes.country, how='left')[expanded_cols]

In [4]:
display (adult_gov_data_expanded.sample(False, 0.01), 250)

age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income alpha_3_code latitude longitude 35.0 ? 129305.0 HS-grad 9.0 Married-civ-spouse ? Husband White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 47.0 Local-gov 186009.0 Some-college 10.0 Divorced Adm-clerical Unmarried White Female 0.0 0.0 38.0 Mexico <=50K MEX 23.0 -102.0 19.0 Private 104112.0 HS-grad 9.0 Never-married Sales Unmarried Black Male 0.0 0.0 30.0 Haiti <=50K HTI 19.0 -72.4167 45.0 Private 261192.0 HS-grad 9.0 Married-civ-spouse Other-service Husband Black Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 59.0 Local-gov 286967.0 HS-grad 9.0 Married-civ-spouse Transport-moving Husband White Male 0.0 0.0 45.0 United States <=50K USA 38.0 -97.0 46.0 Federal-gov 371373.0 HS-grad 9.0 Divorced Adm-clerical Not-in-family White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 52.0 Private 25826.0 10th 6.0 Married-civ-spouse Craft-repair Husband White Male 0.0 1887.0 47.0 United States >50K USA 38.0 -97.0 30.0 Private 103649.0 Bachelors 13.0 Married-civ-spouse Adm-clerical Wife Black Female 0.0 0.0 40.0 United States >50K USA 38.0 -97.0 36.0 Private 131414.0 Some-college 10.0 Never-married Sales Not-in-family Black Female 0.0 0.0 36.0 United States <=50K USA 38.0 -97.0 36.0 Private 51838.0 Some-college 10.0 Divorced Adm-clerical Unmarried White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 44.0 Private 48087.0 Bachelors 13.0 Married-civ-spouse Exec-managerial Husband White Male 0.0 0.0 40.0 United States >50K USA 38.0 -97.0 23.0 Private 153044.0 HS-grad 9.0 Never-married Handlers-cleaners Unmarried Black Female 0.0 0.0 7.0 United States <=50K USA 38.0 -97.0 51.0 Private 269080.0 7th-8th 4.0 Widowed Other-service Unmarried Black Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 50.0 Private 133963.0 Bachelors 13.0 Married-civ-spouse Prof-specialty Wife White Female 0.0 1977.0 40.0 United States >50K USA 38.0 -97.0 55.0 Private 176317.0 HS-grad 9.0 Widowed Adm-clerical Own-child White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 41.0 State-gov 144928.0 Bachelors 13.0 Married-civ-spouse Prof-specialty Husband White Male 0.0 0.0 40.0 United States >50K USA 38.0 -97.0 59.0 Private 296253.0 HS-grad 9.0 Divorced Exec-managerial Not-in-family White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 69.0 ? 473040.0 5th-6th 3.0 Divorced ? Not-in-family White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 46.0 Private 133938.0 Masters 14.0 Divorced Exec-managerial Not-in-family White Female 27828.0 0.0 50.0 United States >50K USA 38.0 -97.0 55.0 Self-emp-not-inc 184425.0 Some-college 10.0 Married-civ-spouse Farming-fishing Husband White Male 0.0 0.0 99.0 United States >50K USA 38.0 -97.0 57.0 Private 185072.0 Some-college 10.0 Never-married Adm-clerical Other-relative Black Female 0.0 0.0 40.0 Jamaica <=50K JAM 18.25 -77.5 28.0 Private 246595.0 HS-grad 9.0 Never-married Craft-repair Own-child White Male 0.0 0.0 70.0 United States <=50K USA 38.0 -97.0 58.0 Local-gov 160586.0 HS-grad 9.0 Married-civ-spouse Farming-fishing Husband White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 47.0 Private 326857.0 Assoc-voc 11.0 Married-civ-spouse Craft-repair Husband White Male 5013.0 0.0 40.0 United States <=50K USA 38.0 -97.0 45.0 Private 339506.0 HS-grad 9.0 Never-married Sales Not-in-family Black Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 29.0 Private 490332.0 Some-college 10.0 Married-civ-spouse Transport-moving Husband White Male 0.0 0.0 45.0 United States >50K USA 38.0 -97.0 21.0 Private 286853.0 HS-grad 9.0 Never-married Other-service Own-child White Male 0.0 0.0 35.0 United States <=50K USA 38.0 -97.0 61.0 Private 153048.0 HS-grad 9.0 Widowed Sales Not-in-family White Female 0.0 0.0 35.0 United States <=50K USA 38.0 -97.0 27.0 Private 217200.0 Some-college 10.0 Never-married Prof-specialty Not-in-family White Male 0.0 0.0 40.

In [5]:
display (adult_gov_data_expanded.describe())

summary age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income alpha_3_code latitude longitude count 32561 32561 32561 32561 32561 32561 32561 32561 32561 32561 32561 32561 32561 32561 32561 31606 31606 31606 mean 38.58164675532078 null 189778.36651208502 null 10.0806793403151 null null null null null 1077.6488437087312 87.303829734959 40.437455852092995 null null null 37.09002754856691 -91.46084107764305 stddev 13.640432553581356 null 105549.97769702227 null 2.572720332067397 null null null null null 7385.292084840354 402.960218649002 12.347428681731838 null null null 5.110597872169294 30.59850465528006 min 17.0 ? 12285.0 10th 1.0 Divorced ? Husband Amer-Indian-Eskimo Female 0.0 0.0 1.0 ? <=50K CAN -10.0 -102.0 max 90.0 Without-pay 1484705.0 Some-college 16.0 Widowed Transport-moving Wife White Male 99999.0 4356.0 99.0 Yugoslavia >50K VNM 60.0 138.0

In [6]:
display(adult_gov_data_expanded.groupBy('alpha_3_code').agg(F.sum('hours_per_week').alias('total_hours')))

alpha_3_code total_hours HTI 1624.0 POL 2300.0 JAM 3126.0 CUB 3720.0 FRA 1307.0 ITA 3037.0 GTM 2511.0 null 39644.0 MEX 25939.0 HUN 463.0 THA 818.0 DOM 2973.0 NIC 1230.0 PER 1097.0 USA 1179861.0 VNM 2502.0 PRT 1550.0 TWN 1983.0 CAN 4889.0 PRI 4397.0 IRL 1018.0 HND 472.0 SLV 3900.0 ECU 1108.0 GRC 1283.0 IND 4153.0 KHM 777.0 CHN 2834.0 DEU 5619.0 JPN 2709.0 PHL 7840.0

In [7]:
col_categorical = ['workclass', 'education', 'marital_status', 'occupation', 'relationship', 'race', 'sex', 'native_country']
pipeline_steps = [] 

for column in col_categorical:
    string_indexed = StringIndexer(inputCol=column, outputCol=column + "Index")
    one_hot_encoded = OneHotEncoderEstimator(inputCols=[string_indexed.getOutputCol()], outputCols=[column + "classVec"])
    pipeline_steps += [string_indexed, one_hot_encoded]
    
label_stringIdx = StringIndexer(inputCol="income", outputCol="label")
pipeline_steps += [label_stringIdx]

numerical_columns = ['age', 'fnlwgt', 'education_num', 'capital_gain', 'capital_loss', 'hours_per_week']
assembler_col = [col + "classVec" for col in col_categorical] + numerical_columns
assemblerModel = VectorAssembler(inputCols=assembler_col, outputCol="features")
pipeline_steps += [assemblerModel]

# Applying the pipeline on the dataset
pipelineInst = Pipeline (stages=pipeline_steps)
pipelineModel = pipelineInst.fit (adult_gov_data_expanded)
adult_gov_data_processed = pipelineModel.transform (adult_gov_data_expanded).select(adult_gov_data_expanded.columns + ['label', 'features'])
train, test = adult_gov_data_processed.randomSplit([.75, .25], seed=121)

In [8]:
display (train.describe())

summary age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income alpha_3_code latitude longitude label count 24386 24386 24386 24386 24386 24386 24386 24386 24386 24386 24386 24386 24386 24386 24386 23650 23650 23650 24386 mean 38.581686213401134 null 189675.10838185844 null 10.100303452800787 null null null null null 1093.426966292135 89.11801853522513 40.41700155827114 null null null 37.08677924735743 -91.29028923044359 0.2413679980316575 stddev 13.62386997654128 null 105774.27339437083 null 2.577346921180809 null null null null null 7492.912946262998 407.98379829801917 12.320523728635731 null null null 5.131110552140711 31.13485399639285 0.4279217179126274 min 17.0 ? 13769.0 10th 1.0 Divorced ? Husband Amer-Indian-Eskimo Female 0.0 0.0 1.0 ? <=50K CAN -10.0 -102.0 0.0 max 90.0 Without-pay 1484705.0 Some-college 16.0 Widowed Transport-moving Wife White Male 99999.0 4356.0 99.0 Yugoslavia >50K VNM 60.0 138.0 1.0

In [9]:
display_cols = ['label', 'age', 'occupation', 'probability', 'prediction']

In [10]:
lrInst = LogisticRegression(labelCol='label', featuresCol='features', maxIter=50)
lrModel = lrInst.fit(train)
lrPredictions = lrModel.transform(test)

lrbceInst = BinaryClassificationEvaluator(rawPredictionCol="rawPrediction")
print ("Model Accuracy = %.15f" % lrbceInst.evaluate(lrPredictions))

Model Accuracy = 0.902831144480752

In [11]:
display (lrPredictions[display_cols])

label age occupation probability prediction 0.0 17.0 ? List(1, 2, List(), List(0.9995291852265232, 4.7081477347669937E-4)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9995686741141787, 4.313258858211785E-4)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9990154651814908, 9.845348185092257E-4)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9997517830442086, 2.4821695579129805E-4)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9989538349801137, 0.0010461650198864013)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9992783383236725, 7.216616763274089E-4)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9997843370346564, 2.1566296534353187E-4)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.999749112688926, 2.5088731107402525E-4)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9989380971078602, 0.0010619028921397965)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.998910170455052, 0.0010898295449478783)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9997688490473584, 2.3115095264159702E-4)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9985354878046396, 0.0014645121953602766)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9992119777964279, 7.880222035721091E-4)) 0.0 0.0 17.0 Protective-serv List(1, 2, List(), List(0.9966114192834409, 0.003388580716559048)) 0.0 0.0 17.0 Craft-repair List(1, 2, List(), List(0.9977603357471891, 0.002239664252810801)) 0.0 0.0 17.0 Adm-clerical List(1, 2, List(), List(0.9993823513989186, 6.176486010814183E-4)) 0.0 0.0 17.0 Exec-managerial List(1, 2, List(), List(0.9961094774930631, 0.0038905225069368926)) 0.0 0.0 17.0 Farming-fishing List(1, 2, List(), List(0.9996557028388758, 3.4429716112419447E-4)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9956684339065012, 0.004331566093498832)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.999637515888333, 3.624841116669119E-4)) 0.0 0.0 17.0 Prof-specialty List(1, 2, List(), List(0.9990185669086785, 9.814330913214264E-4)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.999284313495221, 7.156865047790792E-4)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.999867260229929, 1.327397700710816E-4)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9993667201083902, 6.332798916096365E-4)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9997176691085442, 2.823308914558576E-4)) 0.0 0.0 17.0 Craft-repair List(1, 2, List(), List(0.9996219784702125, 3.7802152978743753E-4)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9980673032228266, 0.0019326967771733153)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9987148555753638, 0.0012851444246362745)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9988244745220214, 0.0011755254779784788)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9994311302570431, 5.68869742956839E-4)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9993299621063132, 6.700378936867853E-4)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9996431496290921, 3.56850370907949E-4)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9994492988143584, 5.507011856416203E-4)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9995458249607282, 4.541750392717924E-4)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9991230127264763, 8.769872735236874E-4)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.999555180456176, 4.448195438241384E-4)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9978779276385943, 0.002122072361405857)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9990949004417214, 9.05099558278563E-4)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9995095509022033, 4.904490977966847E-4)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9993232795661545, 6.767204338454549E-4)) 0.0 0.0 17.0 Prof-specialty List(1, 2, List(), List(0.9979837404328062, 0.002016259567193666)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9993846303162358, 6.153696837642166E-4)) 0.0 0.0 17.0 Transport-moving List(1, 2, List(), List(0.999492718764131, 5.072812358688778E-4)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9995458132603656, 4.5418673963426446

In [12]:
lrpgInst = (ParamGridBuilder()
             .addGrid(lrInst.regParam, [0.01, 0.5, 2.0])
             .addGrid(lrInst.elasticNetParam, [0.0, 0.5, 1.0])
             .addGrid(lrInst.maxIter, [15, 30, 45])
             .build())
lrcvInst = CrossValidator(estimator=lrInst, estimatorParamMaps=lrpgInst, evaluator=lrbceInst, numFolds=5) #5 folds
lrcvModel = lrcvInst.fit(train)
lrcvPredictions = lrcvModel.transform(test)
print ('Best Model Score: %.15f' % lrbceInst.evaluate(lrcvPredictions))
print ('Best Model Intercept: %.15f' % lrcvModel.bestModel.intercept)
new_frame_lrweights = sqlContext.createDataFrame([(float(w),) for w in lrcvModel.bestModel.coefficients], ["Feature Weight"])

Best Model Score: 0.900957475678674
Best Model Intercept: -6.519746213460347

In [13]:
display(new_frame_lrweights)

Feature Weight 0.10284679595328554 -0.31295488161251617 -0.0530022998461281 -0.28383725557485695 -0.21179687049094187 0.31022611816409135 0.6293828591877813 -2.2579864914271077 -0.1837038306507316 -0.0010259397380516565 0.40495741881581426 0.5688005334039815 0.04232817396248483 -0.4851436809476088 -0.050126208109837846 -0.5734779507317957 -0.6067769549929843 0.9208937297307719 -0.6855809095580329 -0.34865790570659005 0.9678325912035045 -0.2653767733124244 -0.8801333943974907 0.7810248974113093 -0.6929801655875087 -0.27514590146074136 -0.49082349094777683 -0.21844091032126683 -0.26415238451372114 0.42349051398359105 0.04599648096968179 0.6792534937932305 -0.05568809666398144 0.26583790346544967 -0.750805360873977 -0.34141927053816806 -0.29999305525906506 -0.14861019851586485 -0.6246711761227394 -0.9880327813418318 0.5936815761498355 0.5327116526940261 -1.4139312982496595 0.520596336918715 -0.0575040209604396 -0.7592158020065627 -0.16307015107903938 1.5260245737697187 0.1632377759185182 -0.033454649252266724 0.06677262767025803 -0.2801913903477458 0.5853405299705318 0.20639029491983515 -0.6017661033657132 -0.02343754127517011 0.41494109235964566 0.4278382839970851 0.1616739750613915 -0.346033994047363 -0.6192577111001271 -0.1662632060193565 0.07763162270183521 0.33825966023527015 0.3214758616284996 -0.8971113848306469 -0.44473496409229824 0.45013974731830725 -1.1284184671627968 -0.7367009500885591 0.007706188440531882 0.5939792340803379 0.15328938906626438 -1.4720031273801806 0.4248013048589259 0.04447219166728447 -0.26250815756062407 -0.0037017051268812898 -0.6019684314364854 -0.7161585766207852 -0.6597902134878747 0.8377173280333262 -0.2647097327465369 0.01395100251052075 -0.32441556032872026 -0.05764252606113089 0.5199115688394979 -0.09046183973032304 -0.26679248969678554 -0.7121443355770349 -1.956621070141533 -1.2055857683364708 -0.600588225857257 0.3461435233075869 0.023453978003811805 7.329649082530469E-7 0.12694198988885164 1.439906982860083E-4 5.522757099821908E-4 0.02701545009997739

In [14]:
display(lrcvPredictions[display_cols])

label age occupation probability prediction 0.0 17.0 ? List(1, 2, List(), List(0.9984893958285243, 0.0015106041714757887)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9984298671990526, 0.0015701328009475087)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.997177829126295, 0.002822170873704959)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9990351540834088, 9.648459165913357E-4)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9970251070100321, 0.002974892989967852)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9973158469657829, 0.0026841530342171225)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9991272727427515, 8.727272572485495E-4)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.999026140234414, 9.738597655858769E-4)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9969863030497849, 0.0030136969502151663)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9969176341262079, 0.0030823658737921655)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9990946247151491, 9.053752848508281E-4)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9959123836940569, 0.004087616305943001)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9976857771063508, 0.0023142228936491893)) 0.0 0.0 17.0 Protective-serv List(1, 2, List(), List(0.991804442716273, 0.008195557283727084)) 0.0 0.0 17.0 Craft-repair List(1, 2, List(), List(0.9941366326174749, 0.0058633673825250945)) 0.0 0.0 17.0 Adm-clerical List(1, 2, List(), List(0.9976987154600679, 0.002301284539932092)) 0.0 0.0 17.0 Exec-managerial List(1, 2, List(), List(0.9890078864263753, 0.010992113573624836)) 0.0 0.0 17.0 Farming-fishing List(1, 2, List(), List(0.9988317263338787, 0.0011682736661212702)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9887690369028557, 0.011230963097144392)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9987627265159797, 0.001237273484020238)) 0.0 0.0 17.0 Prof-specialty List(1, 2, List(), List(0.9966601550392252, 0.0033398449607747096)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9974980014697009, 0.0025019985302990717)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9994260908683783, 5.739091316217308E-4)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9980256909849272, 0.00197430901507292)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9981883335234016, 0.001811666476598348)) 0.0 0.0 17.0 Craft-repair List(1, 2, List(), List(0.9986680311649166, 0.001331968835083221)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9947905494586211, 0.0052094505413788775)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9964618089777869, 0.003538191022213062)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9958911153106379, 0.004108884689362152)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.998242575201977, 0.0017574247980228456)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9977437554347792, 0.002256244565220738)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.998808663720204, 0.001191336279795861)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.998060129072495, 0.001939870927505024)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9985295119272231, 0.0014704880727769362)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9970101868252349, 0.002989813174765199)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9985850241877325, 0.0014149758122673772)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9945976663021451, 0.005402333697854896)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9972986968283577, 0.0027013031716422685)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9984241599931355, 0.0015758400068644034)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.997953063181984, 0.0020469368180161137)) 0.0 0.0 17.0 Prof-specialty List(1, 2, List(), List(0.9941938458357831, 0.005806154164217019)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9978107030719031, 0.0021892969280968766)) 0.0 0.0 17.0 Transport-moving List(1, 2, List(), List(0.9981969031634627, 0.0018030968365374182)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9983596944448454, 0.0016403055

In [15]:
nbInst = NaiveBayes(labelCol='label', featuresCol='features', smoothing=2.0, modelType="multinomial")
nbModel = nbInst.fit(train)
nbPredictions = nbModel.transform(test)
a
nbmceInst = MulticlassClassificationEvaluator(labelCol="label", predictionCol="prediction", metricName="accuracy")
print ("Model Accuracy = %.15f" % nbmceInst.evaluate(nbPredictions))

Model Accuracy = 0.780795107033639

In [16]:
display (nbPredictions[display_cols])

label age occupation probability prediction 0.0 17.0 ? List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 ? List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 ? List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 ? List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 ? List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 ? List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 ? List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 ? List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 ? List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 ? List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 ? List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 ? List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 ? List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Protective-serv List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Craft-repair List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Adm-clerical List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Exec-managerial List(1, 2, List(), List(1.0, 1.279318618604121E-223)) 0.0 0.0 17.0 Farming-fishing List(1, 2, List(), List(1.0, 2.1537832396083705E-305)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(1.0, 2.682325271409796E-308)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Prof-specialty List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Craft-repair List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.2778280479419023E-98, 1.0)) 1.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(1.0, 2.041963426386057E-122)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Prof-specialty List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Transport-moving List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Protective-serv List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Adm-clerical List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Craft-repair List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 17

In [17]:
nbpgInst = (ParamGridBuilder()
             .addGrid(nbInst.smoothing, [1.0, 2.0, 3.0, 4.0, 5.0])
             .build())
nbcvInst = CrossValidator(estimator=nbInst, estimatorParamMaps=nbpgInst, evaluator=nbmceInst, numFolds=5) #5 folds
nbcvModel = nbcvInst.fit(train)
nbcvBestPredictions = nbcvModel.transform(test)
print ('Best Model Score: %.15f' % nbmceInst.evaluate(nbcvBestPredictions))

Best Model Score: 0.780795107033639

In [18]:
display(nbcvBestPredictions)

age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income alpha_3_code latitude longitude label features rawPrediction probability prediction 17.0 ? 47407.0 11th 7.0 Never-married ? Own-child White Male 0.0 0.0 10.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 47407.0, 7.0, 10.0)) List(1, 2, List(), List(-481.4571733052232, -1503.1024106107902)) List(1, 2, List(), List(1.0, 0.0)) 0.0 17.0 ? 86786.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 86786.0, 6.0, 40.0)) List(1, 2, List(), List(-774.4349671804495, -2637.4436206472974)) List(1, 2, List(), List(1.0, 0.0)) 0.0 17.0 ? 89870.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 89870.0, 6.0, 40.0)) List(1, 2, List(), List(-791.8046641768052, -2720.7069971978494)) List(1, 2, List(), List(1.0, 0.0)) 0.0 17.0 ? 158762.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 20.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 158762.0, 6.0, 20.0)) List(1, 2, List(), List(-714.702559991093, -4125.809263367621)) List(1, 2, List(), List(1.0, 0.0)) 0.0 17.0 ? 161981.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 161981.0, 6.0, 40.0)) List(1, 2, List(), List(-902.2371323389249, -4379.232743050699)) List(1, 2, List(), List(1.0, 0.0)) 0.0 17.0 ? 166759.0 12th 8.0 Never-married ? Own-child White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 19, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 166759.0, 8.0, 40.0)) List(1, 2, List(), List(-917.495686148562, -4496.77387381484)) List(1, 2, List(), List(1.0, 0.0)) 0.0 17.0 ? 170320.0 11th 7.0 Never-married ? Own-child White Female 0.0 0.0 8.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 170320.0, 7.0, 8.0)) List(1, 2, List(), List(-640.046409019491, -4301.016898437263)) List(1, 2, List(), List(1.0, 0.0)) 0.0 17.0 ? 171461.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 20.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 171461.0, 6.0, 20.0)) List(1, 2, List(), List(-734.1501049314039, -4417.881463816725)) List(1, 2, List(), List(1.0, 0.0)) 0.0 17.0 ? 179715.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 179715.0, 6.0, 40.0)) List(1, 2, List(), List(-929.395393774587, -4787.108040535888)) List(1, 2, List(), List(1.0, 0.0)) 0.0 17.0 ? 210547.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 210547.0, 6.0, 40.0)) List(1, 2, List(), List(-976.6122380615124, -5496.232387669266)) List(1, 2, List(), List(1.0, 0.0)) 0.0 17.0 ? 256173.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 15.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 256173.0, 6

In [19]:
lrPrevBestModel = lrcvModel.bestModel
ovalrInst = LogisticRegression(labelCol='label', featuresCol='features', fitIntercept=True, 
                               maxIter=lrPrevBestModel._java_obj.getMaxIter(), 
                               elasticNetParam=lrPrevBestModel._java_obj.getElasticNetParam(), 
                               regParam=lrPrevBestModel._java_obj.getRegParam())
ovaInst = OneVsRest(classifier=ovalrInst)
ovaModel = ovaInst.fit(train)
ovaPredictions = ovaModel.transform(test)

ovamceInst = MulticlassClassificationEvaluator(metricName="accuracy")
print ("Model Accuracy = %.15f" % ovamceInst.evaluate(ovaPredictions))

Model Accuracy = 0.847706422018349

In [20]:
display (ovaPredictions)

age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income alpha_3_code latitude longitude label features prediction 17.0 ? 47407.0 11th 7.0 Never-married ? Own-child White Male 0.0 0.0 10.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 47407.0, 7.0, 10.0)) 0.0 17.0 ? 86786.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 86786.0, 6.0, 40.0)) 0.0 17.0 ? 89870.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 89870.0, 6.0, 40.0)) 0.0 17.0 ? 158762.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 20.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 158762.0, 6.0, 20.0)) 0.0 17.0 ? 161981.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 161981.0, 6.0, 40.0)) 0.0 17.0 ? 166759.0 12th 8.0 Never-married ? Own-child White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 19, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 166759.0, 8.0, 40.0)) 0.0 17.0 ? 170320.0 11th 7.0 Never-married ? Own-child White Female 0.0 0.0 8.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 170320.0, 7.0, 8.0)) 0.0 17.0 ? 171461.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 20.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 171461.0, 6.0, 20.0)) 0.0 17.0 ? 179715.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 179715.0, 6.0, 40.0)) 0.0 17.0 ? 210547.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 210547.0, 6.0, 40.0)) 0.0 17.0 ? 256173.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 15.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 256173.0, 6.0, 15.0)) 0.0 17.0 ? 303317.0 11th 7.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 303317.0, 7.0, 40.0)) 0.0 17.0 ? 371316.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 25.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 371316.0, 6.0, 25.0)) 0.0 17.0 Local-gov 175587.0 11th 7.0 Never-married Protective-serv Own-child White Male 0.0 0.0 30.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(2, 13, 24, 41, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 175587.0, 7.0, 30.0)) 0.0 17.0 Local-gov 195262.0 11th 7.0 Never-married Craft-repair Own-child White Male 0.0 0.0 35.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(2, 13, 24, 30, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.

In [21]:
dtInst = DecisionTreeClassifier (labelCol="label", featuresCol="features", maxDepth=4)
dtModel = dtInst.fit (train)
dtPredictions = dtModel.transform (test)
dtbceInst = BinaryClassificationEvaluator()
print ('Model Fit Score: %.15f' % dtbceInst.evaluate(dtPredictions))

Model Fit Score: 0.759812583778094

In [22]:
display(dtPredictions[display_cols])

label age occupation probability prediction 0.0 17.0 ? List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Protective-serv List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Craft-repair List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Adm-clerical List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Exec-managerial List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Farming-fishing List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Prof-specialty List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Craft-repair List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Prof-specialty List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Transport-moving List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9849181100506658, 0.015081889949334275)) 

In [23]:
dtpgInst = (ParamGridBuilder()
             .addGrid(dtInst.maxDepth, [1, 3, 8, 12])
             .addGrid(dtInst.maxBins, [25, 50, 90])
             .build())
dtcvInst = CrossValidator(estimator=dtInst, estimatorParamMaps=dtpgInst, evaluator=dtbceInst, numFolds=5) #5 folds
dtcvModel = dtcvInst.fit(train)
dtcvBestPredictions = dtcvModel.transform(test)
print ('Best Model Score: %.15f' % dtbceInst.evaluate(dtcvBestPredictions))

Best Model Score: 0.795432315523721

In [24]:
display(dtcvBestPredictions[display_cols])

label age occupation probability prediction 0.0 17.0 ? List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Protective-serv List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Craft-repair List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Adm-clerical List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Exec-managerial List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Farming-fishing List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Prof-specialty List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Craft-repair List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Prof-specialty List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Transport-moving List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9972826086956522, 0.002717391304347826)) 

In [25]:
gbtInst = GBTClassifier (labelCol="label", featuresCol="features", maxIter=20, maxDepth=5)
gbtModel = gbtInst.fit (train)
gbtPredictions = gbtModel.transform (test)
gbtmceInst = MulticlassClassificationEvaluator(labelCol="label", predictionCol="prediction", metricName="accuracy")
print ('Model Fit Score: %.15f' % gbtmceInst.evaluate(gbtPredictions))

Model Fit Score: 0.855412844036697

In [26]:
display(gbtPredictions[display_cols])

label age occupation probability prediction 0.0 17.0 ? List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Protective-serv List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Craft-repair List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Adm-clerical List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Exec-managerial List(1, 2, List(), List(0.9482779078411664, 0.05172209215883361)) 0.0 0.0 17.0 Farming-fishing List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Prof-specialty List(1, 2, List(), List(0.9528727458213906, 0.04712725417860941)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Craft-repair List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9506342163473213, 0.04936578365267874)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9506342163473213, 0.04936578365267874)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Prof-specialty List(1, 2, List(), List(0.9528727458213906, 0.04712725417860941)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Transport-moving List(1, 2, List(), List(0.9539880436433699, 0.046011956356630135)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9506342163473213, 0.04936578365267874)) 0.0 0.

In [27]:
gbtpgInst = (ParamGridBuilder()
             .addGrid(gbtInst.maxDepth, [3, 5, 7])
             .addGrid(gbtInst.maxIter, [25, 40, 50])
             .build())
gbtcvInst = CrossValidator(estimator=gbtInst, estimatorParamMaps=gbtpgInst, evaluator=gbtmceInst, numFolds=5) #5 folds
gbtcvModel = gbtcvInst.fit(train)
gbtcvBestPredictions = gbtcvModel.transform(test)
print ('Best Model Score: %.15f' % gbtmceInst.evaluate(gbtcvBestPredictions))

Best Model Score: 0.856880733944954

In [28]:
display (gbtcvBestPredictions)

age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income alpha_3_code latitude longitude label features rawPrediction probability prediction 17.0 ? 47407.0 11th 7.0 Never-married ? Own-child White Male 0.0 0.0 10.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 47407.0, 7.0, 10.0)) List(1, 2, List(), List(1.906925294069026, -1.906925294069026)) List(1, 2, List(), List(0.9784132111774687, 0.02158678882253129)) 0.0 17.0 ? 86786.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 86786.0, 6.0, 40.0)) List(1, 2, List(), List(1.905824604163853, -1.905824604163853)) List(1, 2, List(), List(0.9783666672763492, 0.021633332723650756)) 0.0 17.0 ? 89870.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 89870.0, 6.0, 40.0)) List(1, 2, List(), List(1.905824604163853, -1.905824604163853)) List(1, 2, List(), List(0.9783666672763492, 0.021633332723650756)) 0.0 17.0 ? 158762.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 20.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 158762.0, 6.0, 20.0)) List(1, 2, List(), List(1.906925294069026, -1.906925294069026)) List(1, 2, List(), List(0.9784132111774687, 0.02158678882253129)) 0.0 17.0 ? 161981.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 161981.0, 6.0, 40.0)) List(1, 2, List(), List(1.905824604163853, -1.905824604163853)) List(1, 2, List(), List(0.9783666672763492, 0.021633332723650756)) 0.0 17.0 ? 166759.0 12th 8.0 Never-married ? Own-child White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 19, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 166759.0, 8.0, 40.0)) List(1, 2, List(), List(1.905824604163853, -1.905824604163853)) List(1, 2, List(), List(0.9783666672763492, 0.021633332723650756)) 0.0 17.0 ? 170320.0 11th 7.0 Never-married ? Own-child White Female 0.0 0.0 8.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 170320.0, 7.0, 8.0)) List(1, 2, List(), List(1.906925294069026, -1.906925294069026)) List(1, 2, List(), List(0.9784132111774687, 0.02158678882253129)) 0.0 17.0 ? 171461.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 20.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 171461.0, 6.0, 20.0)) List(1, 2, List(), List(1.906925294069026, -1.906925294069026)) List(1, 2, List(), List(0.9784132111774687, 0.02158678882253129)) 0.0 17.0 ? 179715.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 179715.0, 6.0, 40.0)) List(1, 2, List(), List(1.905824604163853, -1.905824604163853)) List(1, 2, List(), List(0.9783666672763492, 0.021633332723650756)) 0.0 17.0 ? 210547.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 210547.0, 6.0, 40.0)) List(1, 2, List(), List(1.905824604163853, -1.905824604163853)

In [29]:
rfInst = RandomForestClassifier(labelCol="label", featuresCol="features")
rfModel = rfInst.fit(train)
rfPredictions = rfModel.transform(test)
rfbceInst = BinaryClassificationEvaluator()
print ('Model Fit Score: %.15f' % rfbceInst.evaluate(rfPredictions))

Model Fit Score: 0.890150163238809

In [30]:
display (rfPredictions[display_cols])

label age occupation probability prediction 0.0 17.0 ? List(1, 2, List(), List(0.9647656715281634, 0.03523432847183654)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9779761302760008, 0.02202386972399928)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9647656715281634, 0.03523432847183654)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9774397243155428, 0.022560275684457204)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9642292655677055, 0.035770734432294456)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9774397243155428, 0.022560275684457204)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9774397243155428, 0.022560275684457204)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9774397243155428, 0.022560275684457204)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9642292655677055, 0.035770734432294456)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9642292655677055, 0.035770734432294456)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9774397243155428, 0.022560275684457204)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9642292655677055, 0.035770734432294456)) 0.0 0.0 17.0 ? List(1, 2, List(), List(0.9642292655677055, 0.035770734432294456)) 0.0 0.0 17.0 Protective-serv List(1, 2, List(), List(0.9643905295170676, 0.03560947048293244)) 0.0 0.0 17.0 Craft-repair List(1, 2, List(), List(0.9643905295170676, 0.03560947048293244)) 0.0 0.0 17.0 Adm-clerical List(1, 2, List(), List(0.9776009882649049, 0.022399011735095183)) 0.0 0.0 17.0 Exec-managerial List(1, 2, List(), List(0.9780139294863078, 0.021986070513692214)) 0.0 0.0 17.0 Farming-fishing List(1, 2, List(), List(0.9763179962306715, 0.02368200376932847)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9624696066694846, 0.037530393330515416)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.983335077337669, 0.016664922662331057)) 0.0 0.0 17.0 Prof-specialty List(1, 2, List(), List(0.9643000484081865, 0.035699951591813585)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9786920894767256, 0.021307910523274447)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9868478428500532, 0.013152157149946778)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.983335077337669, 0.016664922662331057)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9625437246405543, 0.03745627535944566)) 0.0 0.0 17.0 Craft-repair List(1, 2, List(), List(0.9786920894767256, 0.021307910523274447)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9624696066694846, 0.037530393330515416)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9651609939188898, 0.03483900608111022)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9868478428500532, 0.013152157149946778)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9654816307288883, 0.03451836927111171)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.983335077337669, 0.016664922662331057)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.983335077337669, 0.016664922662331057)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9786920894767256, 0.021307910523274447)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.983335077337669, 0.016664922662331057)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9786920894767256, 0.021307910523274447)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9651609939188898, 0.03483900608111022)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9654816307288883, 0.03451836927111171)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.983335077337669, 0.016664922662331057)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.983335077337669, 0.016664922662331057)) 0.0 0.0 17.0 Handlers-cleaners List(1, 2, List(), List(0.9654816307288883, 0.03451836927111171)) 0.0 0.0 17.0 Prof-specialty List(1, 2, List(), List(0.9427154704614876, 0.05728452953851231)) 0.0 0.0 17.0 Sales List(1, 2, List(), List(0.9786920894767256, 0.021307910523274447)) 0.0 0.0 17.0 Transport-moving List(1, 2, List(), List(0.9786920894767256, 0.021307910523274447)) 0.0 0.0 17.0 Other-service List(1, 2, List(), List(0.9868478428500532, 0.013152157149946778)) 0.0 0.0 17.0 Sales L

In [31]:
rfpgInst = (ParamGridBuilder()
             .addGrid(rfInst.maxDepth, [1, 3, 8])
             .addGrid(rfInst.maxBins, [25, 50])
             .addGrid(rfInst.numTrees, [5, 20])
             .build())
rfcvInst = CrossValidator(estimator=rfInst, estimatorParamMaps=rfpgInst, evaluator=rfbceInst, numFolds=5)
rfcvModel = rfcvInst.fit(train)
rfcvBestPredictions = rfcvModel.transform(test)
print ('Best Model Score: %.15f' % rfbceInst.evaluate(rfcvBestPredictions))

Best Model Score: 0.903182868561979

In [32]:
display (rfcvBestPredictions)

age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income alpha_3_code latitude longitude label features rawPrediction probability prediction 17.0 ? 47407.0 11th 7.0 Never-married ? Own-child White Male 0.0 0.0 10.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 47407.0, 7.0, 10.0)) List(1, 2, List(), List(19.832105485565403, 0.16789451443459927)) List(1, 2, List(), List(0.9916052742782699, 0.008394725721729963)) 0.0 17.0 ? 86786.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 86786.0, 6.0, 40.0)) List(1, 2, List(), List(19.81839571368025, 0.18160428631975262)) List(1, 2, List(), List(0.9909197856840123, 0.00908021431598763)) 0.0 17.0 ? 89870.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 89870.0, 6.0, 40.0)) List(1, 2, List(), List(19.811886699516585, 0.18811330048341662)) List(1, 2, List(), List(0.9905943349758293, 0.00940566502417083)) 0.0 17.0 ? 158762.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 20.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 158762.0, 6.0, 20.0)) List(1, 2, List(), List(19.828128073777574, 0.17187192622242903)) List(1, 2, List(), List(0.9914064036888786, 0.00859359631112145)) 0.0 17.0 ? 161981.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 161981.0, 6.0, 40.0)) List(1, 2, List(), List(19.811886699516585, 0.18811330048341662)) List(1, 2, List(), List(0.9905943349758293, 0.00940566502417083)) 0.0 17.0 ? 166759.0 12th 8.0 Never-married ? Own-child White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 19, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 166759.0, 8.0, 40.0)) List(1, 2, List(), List(19.821515838485244, 0.1784841615147604)) List(1, 2, List(), List(0.991075791924262, 0.008924208075738018)) 0.0 17.0 ? 170320.0 11th 7.0 Never-married ? Own-child White Female 0.0 0.0 8.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 170320.0, 7.0, 8.0)) List(1, 2, List(), List(19.84173462453406, 0.15826537546594302)) List(1, 2, List(), List(0.9920867312267028, 0.00791326877329715)) 0.0 17.0 ? 171461.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 20.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 171461.0, 6.0, 20.0)) List(1, 2, List(), List(19.831248198582568, 0.16875180141743681)) List(1, 2, List(), List(0.9915624099291283, 0.00843759007087184)) 0.0 17.0 ? 179715.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 179715.0, 6.0, 40.0)) List(1, 2, List(), List(19.813161805871392, 0.18683819412860891)) List(1, 2, List(), List(0.9906580902935695, 0.009341909706430446)) 0.0 17.0 ? 210547.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 210547.0, 6.0, 40.0)) List(1, 2, List(), List(19.813161805871392, 0.1868

In [33]:
rfPrevBestModel = rfcvModel.bestModel
ovarfInst = RandomForestClassifier(labelCol='label', featuresCol='features',
                               maxDepth=rfPrevBestModel._java_obj.getMaxDepth(), 
                               maxBins=rfPrevBestModel._java_obj.getMaxBins(), 
                               numTrees=rfPrevBestModel._java_obj.getNumTrees())
ovarfInst = OneVsRest(classifier=ovarfInst)
ovarfModel = ovarfInst.fit(train)
ovarfPredictions = ovarfModel.transform(test)

ovamceInst = MulticlassClassificationEvaluator(metricName="accuracy")
print ("Model Accuracy = %.15f" % ovamceInst.evaluate(ovarfPredictions))

Model Accuracy = 0.848440366972477

In [34]:
display (ovarfPredictions)

age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income alpha_3_code latitude longitude label features prediction 17.0 ? 47407.0 11th 7.0 Never-married ? Own-child White Male 0.0 0.0 10.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 47407.0, 7.0, 10.0)) 0.0 17.0 ? 86786.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 86786.0, 6.0, 40.0)) 0.0 17.0 ? 89870.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 89870.0, 6.0, 40.0)) 0.0 17.0 ? 158762.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 20.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 158762.0, 6.0, 20.0)) 0.0 17.0 ? 161981.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 161981.0, 6.0, 40.0)) 0.0 17.0 ? 166759.0 12th 8.0 Never-married ? Own-child White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 19, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 166759.0, 8.0, 40.0)) 0.0 17.0 ? 170320.0 11th 7.0 Never-married ? Own-child White Female 0.0 0.0 8.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 170320.0, 7.0, 8.0)) 0.0 17.0 ? 171461.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 20.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 171461.0, 6.0, 20.0)) 0.0 17.0 ? 179715.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 179715.0, 6.0, 40.0)) 0.0 17.0 ? 210547.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 210547.0, 6.0, 40.0)) 0.0 17.0 ? 256173.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 15.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 256173.0, 6.0, 15.0)) 0.0 17.0 ? 303317.0 11th 7.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 303317.0, 7.0, 40.0)) 0.0 17.0 ? 371316.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 25.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 371316.0, 6.0, 25.0)) 0.0 17.0 Local-gov 175587.0 11th 7.0 Never-married Protective-serv Own-child White Male 0.0 0.0 30.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(2, 13, 24, 41, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 175587.0, 7.0, 30.0)) 0.0 17.0 Local-gov 195262.0 11th 7.0 Never-married Craft-repair Own-child White Male 0.0 0.0 35.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(2, 13, 24, 30, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.

In [35]:
layers = [train.schema["features"].metadata["ml_attr"]["num_attrs"], 20, 10, 2]
mpcInst = MultilayerPerceptronClassifier(maxIter=100, layers=layers, blockSize=128, seed=451)
mpcModel = mpcInst.fit(train)
mpcPredictions = mpcModel.transform(test)
mpcBce = MulticlassClassificationEvaluator(metricName="accuracy")
print ("Model Accuracy = %.15f" % mpcBce.evaluate(mpcPredictions))

Model Accuracy = 0.767584097859327

In [36]:
display (mpcPredictions)

age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income alpha_3_code latitude longitude label features rawPrediction probability prediction 17.0 ? 47407.0 11th 7.0 Never-married ? Own-child White Male 0.0 0.0 10.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 47407.0, 7.0, 10.0)) List(1, 2, List(), List(0.953811992394703, -0.22494370514379952)) List(1, 2, List(), List(0.7647240011164417, 0.23527599888355832)) 0.0 17.0 ? 86786.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 86786.0, 6.0, 40.0)) List(1, 2, List(), List(0.953811992394703, -0.22494370514379952)) List(1, 2, List(), List(0.7647240011164417, 0.23527599888355832)) 0.0 17.0 ? 89870.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 89870.0, 6.0, 40.0)) List(1, 2, List(), List(0.953811992394703, -0.22494370514379952)) List(1, 2, List(), List(0.7647240011164417, 0.23527599888355832)) 0.0 17.0 ? 158762.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 20.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 158762.0, 6.0, 20.0)) List(1, 2, List(), List(0.953811992394703, -0.22494370514379952)) List(1, 2, List(), List(0.7647240011164417, 0.23527599888355832)) 0.0 17.0 ? 161981.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 161981.0, 6.0, 40.0)) List(1, 2, List(), List(0.953811992394703, -0.22494370514379952)) List(1, 2, List(), List(0.7647240011164417, 0.23527599888355832)) 0.0 17.0 ? 166759.0 12th 8.0 Never-married ? Own-child White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 19, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 166759.0, 8.0, 40.0)) List(1, 2, List(), List(0.953811992394703, -0.22494370514379952)) List(1, 2, List(), List(0.7647240011164417, 0.23527599888355832)) 0.0 17.0 ? 170320.0 11th 7.0 Never-married ? Own-child White Female 0.0 0.0 8.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 170320.0, 7.0, 8.0)) List(1, 2, List(), List(0.953811992394703, -0.22494370514379952)) List(1, 2, List(), List(0.7647240011164417, 0.23527599888355832)) 0.0 17.0 ? 171461.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 20.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 171461.0, 6.0, 20.0)) List(1, 2, List(), List(0.953811992394703, -0.22494370514379952)) List(1, 2, List(), List(0.7647240011164417, 0.23527599888355832)) 0.0 17.0 ? 179715.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 179715.0, 6.0, 40.0)) List(1, 2, List(), List(0.953811992394703, -0.22494370514379952)) List(1, 2, List(), List(0.7647240011164417, 0.23527599888355832)) 0.0 17.0 ? 210547.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 210547.0, 6.0, 40.0)) List(1, 2, List(), List(0.953811992394703, -0.224

In [37]:
mpcpgInst = (ParamGridBuilder()
             .addGrid(mpcInst.maxIter, [50, 100, 150])
             .addGrid(mpcInst.blockSize, [128, 256, 512])
             .build())
mpccvInst = CrossValidator(estimator=mpcInst, estimatorParamMaps=mpcpgInst, evaluator=mpcBce, numFolds=5)
mpccvModel = mpccvInst.fit(train)
mpccvBestPredictions = mpccvModel.transform(test)
print ("Best Model Accuracy Score = %.15f" % mpcBce.evaluate(mpccvBestPredictions))

Best Model Accuracy Score = 0.767461773700306

In [38]:
display (mpccvBestPredictions)

age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income alpha_3_code latitude longitude label features rawPrediction probability prediction 17.0 ? 47407.0 11th 7.0 Never-married ? Own-child White Male 0.0 0.0 10.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 47407.0, 7.0, 10.0)) List(1, 2, List(), List(0.6876307671197011, -0.4942175011979356)) List(1, 2, List(), List(0.7652799645741133, 0.23472003542588674)) 0.0 17.0 ? 86786.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 86786.0, 6.0, 40.0)) List(1, 2, List(), List(0.6876307671197011, -0.4942175011979356)) List(1, 2, List(), List(0.7652799645741133, 0.23472003542588674)) 0.0 17.0 ? 89870.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 89870.0, 6.0, 40.0)) List(1, 2, List(), List(0.6876307671197011, -0.4942175011979356)) List(1, 2, List(), List(0.7652799645741133, 0.23472003542588674)) 0.0 17.0 ? 158762.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 20.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 158762.0, 6.0, 20.0)) List(1, 2, List(), List(0.6876307671197011, -0.4942175011979356)) List(1, 2, List(), List(0.7652799645741133, 0.23472003542588674)) 0.0 17.0 ? 161981.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 161981.0, 6.0, 40.0)) List(1, 2, List(), List(0.6876307671197011, -0.4942175011979356)) List(1, 2, List(), List(0.7652799645741133, 0.23472003542588674)) 0.0 17.0 ? 166759.0 12th 8.0 Never-married ? Own-child White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 19, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 166759.0, 8.0, 40.0)) List(1, 2, List(), List(0.6876307671197011, -0.4942175011979356)) List(1, 2, List(), List(0.7652799645741133, 0.23472003542588674)) 0.0 17.0 ? 170320.0 11th 7.0 Never-married ? Own-child White Female 0.0 0.0 8.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 13, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 170320.0, 7.0, 8.0)) List(1, 2, List(), List(0.6876307671197011, -0.4942175011979356)) List(1, 2, List(), List(0.7652799645741133, 0.23472003542588674)) 0.0 17.0 ? 171461.0 10th 6.0 Never-married ? Own-child White Female 0.0 0.0 20.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 171461.0, 6.0, 20.0)) List(1, 2, List(), List(0.6876307671197011, -0.4942175011979356)) List(1, 2, List(), List(0.7652799645741133, 0.23472003542588674)) 0.0 17.0 ? 179715.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 179715.0, 6.0, 40.0)) List(1, 2, List(), List(0.6876307671197011, -0.4942175011979356)) List(1, 2, List(), List(0.7652799645741133, 0.23472003542588674)) 0.0 17.0 ? 210547.0 10th 6.0 Never-married ? Own-child White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(3, 15, 24, 36, 45, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 17.0, 210547.0, 6.0, 40.0)) List(1, 2, List(), List(0.6876307671197011, -0.49

In [39]:
selectedModel = rfcvModel.bestModel
selectedPredictions = selectedModel.transform(adult_gov_data_processed)
print ("Model Fit Score = ", rfbceInst.evaluate(selectedPredictions))

Model Fit Score = 0.9113447786487396

In [40]:
display(selectedPredictions)

age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income alpha_3_code latitude longitude label features rawPrediction probability prediction 39.0 State-gov 77516.0 Bachelors 13.0 Never-married Adm-clerical Not-in-family White Male 2174.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(4, 10, 24, 32, 44, 48, 52, 53, 94, 95, 96, 97, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 39.0, 77516.0, 13.0, 2174.0, 40.0)) List(1, 2, List(), List(17.917590901421665, 2.0824090985783323)) List(1, 2, List(), List(0.8958795450710834, 0.10412045492891664)) 0.0 50.0 Self-emp-not-inc 83311.0 Bachelors 13.0 Married-civ-spouse Exec-managerial Husband White Male 0.0 0.0 13.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(1, 10, 23, 31, 43, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 50.0, 83311.0, 13.0, 13.0)) List(1, 2, List(), List(7.898398051088204, 12.101601948911796)) List(1, 2, List(), List(0.39491990255441023, 0.6050800974455898)) 1.0 38.0 Private 215646.0 HS-grad 9.0 Divorced Handlers-cleaners Not-in-family White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(0, 8, 25, 38, 44, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 38.0, 215646.0, 9.0, 40.0)) List(1, 2, List(), List(18.718690776480567, 1.2813092235194286)) List(1, 2, List(), List(0.9359345388240286, 0.06406546117597144)) 0.0 53.0 Private 234721.0 11th 7.0 Married-civ-spouse Handlers-cleaners Husband Black Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(0, 13, 23, 38, 43, 49, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 53.0, 234721.0, 7.0, 40.0)) List(1, 2, List(), List(14.362465642341656, 5.637534357658344)) List(1, 2, List(), List(0.7181232821170828, 0.28187671788291724)) 0.0 28.0 Private 338409.0 Bachelors 13.0 Married-civ-spouse Prof-specialty Wife Black Female 0.0 0.0 40.0 Cuba <=50K CUB 21.5 -80.0 0.0 List(0, 100, List(0, 10, 23, 29, 47, 49, 62, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 28.0, 338409.0, 13.0, 40.0)) List(1, 2, List(), List(10.28674916937619, 9.713250830623808)) List(1, 2, List(), List(0.5143374584688095, 0.48566254153119043)) 0.0 37.0 Private 284582.0 Masters 14.0 Married-civ-spouse Exec-managerial Wife White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(0, 11, 23, 31, 47, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 37.0, 284582.0, 14.0, 40.0)) List(1, 2, List(), List(9.111774750436037, 10.88822524956396)) List(1, 2, List(), List(0.45558873752180185, 0.544411262478198)) 1.0 49.0 Private 160187.0 9th 5.0 Married-spouse-absent Other-service Not-in-family Black Female 0.0 0.0 16.0 Jamaica <=50K JAM 18.25 -77.5 0.0 List(0, 100, List(0, 18, 28, 34, 44, 49, 64, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 49.0, 160187.0, 5.0, 16.0)) List(1, 2, List(), List(19.2238734485469, 0.776126551453101)) List(1, 2, List(), List(0.961193672427345, 0.03880632757265505)) 0.0 52.0 Self-emp-not-inc 209642.0 HS-grad 9.0 Married-civ-spouse Exec-managerial Husband White Male 0.0 0.0 45.0 United States >50K USA 38.0 -97.0 1.0 List(0, 100, List(1, 8, 23, 31, 43, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 52.0, 209642.0, 9.0, 45.0)) List(1, 2, List(), List(11.803534864169333, 8.196465135830667)) List(1, 2, List(), List(0.5901767432084666, 0.40982325679153336)) 0.0 31.0 Private 45781.0 Masters 14.0 Never-married Prof-specialty Not-in-family White Female 14084.0 0.0 50.0 United States >50K USA 38.0 -97.0 1.0 List(0, 100, List(0, 11, 24, 29, 44, 48, 53, 94, 95, 96, 97, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 31.0, 45781.0, 14.0, 14084.0, 50.0)) List(1, 2, List(), List(5.989804833295561, 14.010195166704438)) List(1, 2, List(), List(0.29949024166477806, 0.7005097583352219)) 1.0 42.0 Private 159449.0 Bachelors 13.0 Mar

In [41]:
display(selectedPredictions)

age workclass fnlwgt education education_num marital_status occupation relationship race sex capital_gain capital_loss hours_per_week native_country income alpha_3_code latitude longitude label features rawPrediction probability prediction 39.0 State-gov 77516.0 Bachelors 13.0 Never-married Adm-clerical Not-in-family White Male 2174.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(4, 10, 24, 32, 44, 48, 52, 53, 94, 95, 96, 97, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 39.0, 77516.0, 13.0, 2174.0, 40.0)) List(1, 2, List(), List(17.917590901421665, 2.0824090985783323)) List(1, 2, List(), List(0.8958795450710834, 0.10412045492891664)) 0.0 50.0 Self-emp-not-inc 83311.0 Bachelors 13.0 Married-civ-spouse Exec-managerial Husband White Male 0.0 0.0 13.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(1, 10, 23, 31, 43, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 50.0, 83311.0, 13.0, 13.0)) List(1, 2, List(), List(7.898398051088204, 12.101601948911796)) List(1, 2, List(), List(0.39491990255441023, 0.6050800974455898)) 1.0 38.0 Private 215646.0 HS-grad 9.0 Divorced Handlers-cleaners Not-in-family White Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(0, 8, 25, 38, 44, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 38.0, 215646.0, 9.0, 40.0)) List(1, 2, List(), List(18.718690776480567, 1.2813092235194286)) List(1, 2, List(), List(0.9359345388240286, 0.06406546117597144)) 0.0 53.0 Private 234721.0 11th 7.0 Married-civ-spouse Handlers-cleaners Husband Black Male 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(0, 13, 23, 38, 43, 49, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 53.0, 234721.0, 7.0, 40.0)) List(1, 2, List(), List(14.362465642341656, 5.637534357658344)) List(1, 2, List(), List(0.7181232821170828, 0.28187671788291724)) 0.0 28.0 Private 338409.0 Bachelors 13.0 Married-civ-spouse Prof-specialty Wife Black Female 0.0 0.0 40.0 Cuba <=50K CUB 21.5 -80.0 0.0 List(0, 100, List(0, 10, 23, 29, 47, 49, 62, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 28.0, 338409.0, 13.0, 40.0)) List(1, 2, List(), List(10.28674916937619, 9.713250830623808)) List(1, 2, List(), List(0.5143374584688095, 0.48566254153119043)) 0.0 37.0 Private 284582.0 Masters 14.0 Married-civ-spouse Exec-managerial Wife White Female 0.0 0.0 40.0 United States <=50K USA 38.0 -97.0 0.0 List(0, 100, List(0, 11, 23, 31, 47, 48, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 37.0, 284582.0, 14.0, 40.0)) List(1, 2, List(), List(9.111774750436037, 10.88822524956396)) List(1, 2, List(), List(0.45558873752180185, 0.544411262478198)) 1.0 49.0 Private 160187.0 9th 5.0 Married-spouse-absent Other-service Not-in-family Black Female 0.0 0.0 16.0 Jamaica <=50K JAM 18.25 -77.5 0.0 List(0, 100, List(0, 18, 28, 34, 44, 49, 64, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 49.0, 160187.0, 5.0, 16.0)) List(1, 2, List(), List(19.2238734485469, 0.776126551453101)) List(1, 2, List(), List(0.961193672427345, 0.03880632757265505)) 0.0 52.0 Self-emp-not-inc 209642.0 HS-grad 9.0 Married-civ-spouse Exec-managerial Husband White Male 0.0 0.0 45.0 United States >50K USA 38.0 -97.0 1.0 List(0, 100, List(1, 8, 23, 31, 43, 48, 52, 53, 94, 95, 96, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 52.0, 209642.0, 9.0, 45.0)) List(1, 2, List(), List(11.803534864169333, 8.196465135830667)) List(1, 2, List(), List(0.5901767432084666, 0.40982325679153336)) 0.0 31.0 Private 45781.0 Masters 14.0 Never-married Prof-specialty Not-in-family White Female 14084.0 0.0 50.0 United States >50K USA 38.0 -97.0 1.0 List(0, 100, List(0, 11, 24, 29, 44, 48, 53, 94, 95, 96, 97, 99), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 31.0, 45781.0, 14.0, 14084.0, 50.0)) List(1, 2, List(), List(5.989804833295561, 14.010195166704438)) List(1, 2, List(), List(0.29949024166477806, 0.7005097583352219)) 1.0 42.0 Private 159449.0 Bachelors 13.0 Mar

In [42]:
classifier_comparison_df = spark.createDataFrame(pd.DataFrame({
  'classifiers':['LR', 'NB', 'DT', 'GBT', 'RF', 'MLP', 'ovA-LR', 'ovA-RF'], 
  'accuracy_scores':[90.1, 78.8, 76.7, 85.5, 89.1, 76.5, 84.8, 84.8]
}))
display(classifier_comparison_df)

accuracy_scores classifiers 90.1 LR 78.8 NB 76.7 DT 85.5 GBT 89.1 RF 76.5 MLP 84.8 ovA-LR 84.8 ovA-RF

We implemented all the classifiers available with the Pyspark ML module, and the RF classifier emerged with the best accuracy for this dataset with a score of 90.6%. We plan to implement XGBoost on the same data in the future notebooks. <br/> 

For the best models against each classifier, the below-mentioned accuracy scores were achieved: <br/>

<ul>
  <li> Logistic Regression - 90.1% </li>
  <li> Naive Bayes - 78.8% </li>
  <li> Decision Tree - 76.7% </li>
  <li> Gradient-boosted Tree - 85.5% </li>
  <li> Random Forest - 89.1% </li>
  <li> Multilayer Perceptron - 76.5%</li>
  <li> One-vs-All (Logistic Regression - 84.8%, Random Forest - 84.8%) </li>
</ul>

The published version of the notebook is available at - <br/> 
https://databricks-prod-cloudfront.cloud.databricks.com/public/4027ec902e239c93eaaa8714f173bcfc/3173713035751393/675963439015456/2308983777460038/latest.html